In [1]:
using DifferentialEquations
using Plots

In [2]:
function model(du,u,p,t)
    
    # PARAMATERS
    # Load paramaters
    organic_carbon_input = p[1]
    inorganic_carbon_input = p[2]
    natural_death_fraction = p[3]
    ks = p[4]
    organic_carbon_content_per_cell = p[5]
    inorganic_carbon_content_per_cell = p[6]
    mu_max = p[7]
    growth_penalty = p[8]
    base_maintenance_per_cell = p[9]
    m_prime = p[10]
    maximum_growth_yield = p[11]
    inorganic_carbon_fixing_factor = p[12]
    carrying_capacity = p[13]
    

    # Load state conditions
    organic_carbon_content = u[1]
    inorganic_carbon_content = u[2]
    cell_count = u[3]


    ## CELL COUNT
    # Growth
    penalized_mu_max = mu_max * (1 - growth_penalty)
    growth = penalized_mu_max * (organic_carbon_content / (ks + organic_carbon_content)) * cell_count * (
            1 - cell_count / carrying_capacity)

    # Specific growth rate
    # next_cell_count = cell_count + growth
    # specific_growth_rate = 0
    # if next_cell_count > 0 and cell_count > 0:
    #     specific_growth_rate = max((np.log(next_cell_count) - np.log(cell_count)), 0)

    # Organic carbon requirement
    required_organic_carbon_per_cell = base_maintenance_per_cell  # + m_prime * (1 - specific_growth_rate/mu_max)
    required_organic_carbon = required_organic_carbon_per_cell * cell_count

    # Starvation
    organic_carbon_missing = max(required_organic_carbon - organic_carbon_content, 0)
    
    starvation_deaths = organic_carbon_missing == 0 ? 0 : organic_carbon_missing / required_organic_carbon_per_cell

    # Natural Death
    natural_deaths = natural_death_fraction * cell_count - natural_death_fraction * starvation_deaths

    # Deaths
    deaths = natural_deaths + starvation_deaths

    # Net cell count change
    du[3] = growth - deaths

    ## CARBON
    carbon_consumption = required_organic_carbon_per_cell * (cell_count - deaths)
    fixed_carbon = inorganic_carbon_fixing_factor * inorganic_carbon_content

    # Inorganic carbon
    du[2] = inorganic_carbon_input + inorganic_carbon_content_per_cell * (
            deaths - growth) + carbon_consumption - fixed_carbon

    # Organic carbon
    du[1] = organic_carbon_input + organic_carbon_content_per_cell * (
            deaths - growth) - carbon_consumption + fixed_carbon
    
end

model (generic function with 1 method)

In [3]:
p = [0, 0.0, 0.001, 882000000.0, 140.0, 0.0, 0.0000004, 0.5, 2.1739130434782608, 0.0, 1.0406549188289163, 0.0, 1000000000.0]
duration = 11000 * 365.25 # In days

u0 = [1286820000000.0; 0.0; 100000.0]
tspan = (0.0, duration)
prob = ODEProblem(model,u0,tspan,p)
sol = solve(prob, reltol=1e-9, abstol=1e-9)

S = plot(sol, vars=(1), yaxis="Organic C")
I = plot(sol, vars=(2), yaxis="Inorganic C")
N = plot(sol, vars=(3), yaxis="Cells")


plot(plot(N),plot(I, S, layout=(1,2)), layout=(2,1))